## Part 0: Configure `GLIBC` to most update version

To run GPT4ALL in ubuntu, we need to make sure `GLIBC` is up-to-date.

In [6]:
!ldd --version

ldd (Ubuntu GLIBC 2.31-0ubuntu9.14) 2.31
Copyright (C) 2020 Free Software Foundation, Inc.
This is free software; see the source for copying conditions.  There is NO
warranty; not even for MERCHANTABILITY or FITNESS FOR A PARTICULAR PURPOSE.
Written by Roland McGrath and Ulrich Drepper.


## Part 1: Setup `GPT4ALL`

This notebook is designed for ubuntu(linux) operation system PC.

Go to this page to get installation `.run` file. 

Use the following commands to run the installation file in the terminal:

```bash
cd ~/Downloads
chmod +x gpt4all-installer-linux.run
./gpt4all-installer-linux.run
```

In my trial, the target directory of gpt4all installation is `/home/researcher/gpt4all`.

## Part 2: Creating our `main.py` "app" that put our LLM logic

The following is our component that will be put in `main.py`.

- `main.py` will control how we call the model. 

```python
from gpt4all import GPT4All # line 1 return `GLIBC 2.32` is not found
model = GPT4All("./models/nous-hermes-llama2-13b.Q4_0.gguf")
# model = GPT4All("orca-2-13b.Q4_0.gguf")
output = model.generate("The capital of France is ", max_tokens=3)
print(output)
```

## Part 3: Download a LLM from GPT4ALL and put in on the project folder

- In `main.py`, GPT4ALL can discover the model by `model = GPT4All("./models/nous-hermes-llama2-13b.Q4_0.gguf")`
- Don't forget to specify `.gitignore` so that the whole `models` folder will be ignored by git. 

## Part 4: Create a Docker image as a "wrapper" of the `main.py`

First, we need to test whether our computer has installed docker and it is functional:

In [1]:
!sudo docker run hello-world


Hello from Docker!
This message shows that your installation appears to be working correctly.

To generate this message, Docker took the following steps:
 1. The Docker client contacted the Docker daemon.
 2. The Docker daemon pulled the "hello-world" image from the Docker Hub.
    (amd64)
 3. The Docker daemon created a new container from that image which runs the
    executable that produces the output you are currently reading.
 4. The Docker daemon streamed that output to the Docker client, which sent it
    to your terminal.

To try something more ambitious, you can run an Ubuntu container with:
 $ docker run -it ubuntu bash

Share images, automate workflows, and more with a free Docker ID:
 https://hub.docker.com/

For more examples and ideas, visit:
 https://docs.docker.com/get-started/



## Part 5: Run `main.py` with docker

In Dockerfile, we specify the environnment,

```Dockerfile
# Use the latest Ubuntu image as the base
FROM ubuntu:latest
```

and also specify which command to run `main.py`

```Dockerfile
# Run the Python script
CMD ["python3", "script.py"]
```

So now we can use put those Docker commands here and run the script here.

## Part 5a: Create/edit docker image

(The following command create/updates the docker image)

- `build`: sub-command of docker that is used to create a Docker image from a Dockerfile and a "context". 

- `-t gpt4all-app`: `-t` flags stands for tag. the following is the name of the tag.

- `.`: It signifies the current directory, meaing Docker will look for a Dockerfile in the current directory where the command is run.

In [2]:
!sudo docker build -t gpt4all-app .

[+] Building 0.0s (0/1)                                          docker:default
[+] Building 0.2s (1/2)                                          docker:default
 => [internal] load build definition from Dockerfile                       0.0s
 => => transferring dockerfile: 3.40kB                                     0.0s
 => [internal] load metadata for docker.io/nvidia/cuda:12.3.2-cudnn9-runt  0.2s
[+] Building 0.3s (1/2)                                          docker:default
 => [internal] load build definition from Dockerfile                       0.0s
 => => transferring dockerfile: 3.40kB                                     0.0s
 => [internal] load metadata for docker.io/nvidia/cuda:12.3.2-cudnn9-runt  0.3s
[+] Building 0.5s (1/2)                                          docker:default
 => [internal] load build definition from Dockerfile                       0.0s
 => => transferring dockerfile: 3.40kB                                     0.0s
 => [internal] load metadata for docker.

After the build process is complete, check it whether it exist on the list: 

In [4]:
!sudo docker images

REPOSITORY    TAG       IMAGE ID       CREATED         SIZE
gpt4all-app   latest    d02965c65fcb   3 minutes ago   19.7GB
hello-world   latest    d2c94e258dcb   10 months ago   13.3kB


(Optional: Rename the image)

Note: the process only change tag(pointer), the image would not be affected.

In [5]:
!sudo docker tag gpt4all-app gpt4all-wrapper
!sudo docker rmi gpt4all-app

Untagged: gpt4all-app:latest


In [6]:
!sudo docker images

REPOSITORY        TAG       IMAGE ID       CREATED         SIZE
gpt4all-wrapper   latest    d02965c65fcb   5 minutes ago   19.7GB
hello-world       latest    d2c94e258dcb   10 months ago   13.3kB


## Part 5b: Adding and push Dockerimage to Dockerhub

In [11]:
!sudo docker login

Log in with your Docker ID or email address to push and pull images from Docker Hub. If you don't have a Docker ID, head over to https://hub.docker.com/ to create one.
You can log in with your password or a Personal Access Token (PAT). Using a limited-scope PAT grants better security and is required for organizations using SSO. Learn more at https://docs.docker.com/go/access-tokens/

Username: ^C


(To push an image to Docker hub, the image must be tagged with correct repo name)

Such as `pakkinlau/gpt4all-wrapper`

In [7]:
!sudo docker tag gpt4all-wrapper pakkinlau/gpt4all-wrapper
!sudo docker rmi gpt4all-wrapper

Untagged: gpt4all-wrapper:latest


In [8]:
!sudo docker images

REPOSITORY                  TAG       IMAGE ID       CREATED         SIZE
pakkinlau/gpt4all-wrapper   latest    d02965c65fcb   8 minutes ago   19.7GB
hello-world                 latest    d2c94e258dcb   10 months ago   13.3kB


## Part 6 - Uploading to public

Finally, if the image is well-tested and functional, we can push the image to remote repo as a backup:

In [12]:
!sudo docker push pakkinlau/gpt4all-wrapper

Using default tag: latest
The push refers to repository [docker.io/pakkinlau/gpt4all-wrapper]

f851e592: Preparing 
67f57925: Preparing 
634a2f94: Preparing 
2d2f10bc: Preparing 
8c8411b3: Preparing 
688be0cc: Preparing 
fabd9250: Preparing 
a7fea4a7: Preparing 
ac1b55a1: Preparing 
f939e8ef: Preparing 
20082ab6: Preparing 
89477cd0: Preparing 
a508ec30: Preparing 
0a27585a: Preparing 
852fcfd3: Preparing 
793a3432: Preparing 
54a69fbf: Preparing 
5d3b1182: Preparing 
7f57925: Pushed   7.366GB/7.366GB [17Alatest: digest: sha256:13cec73e314c3aa569f3b59526d943de361dd31a307e3e189fd06e97991f15da size: 4323


(The following command run the docker image)

In [ ]:
!sudo docker run -v $(pwd)/main.py:/app/main.py my_image